In [1]:
import pandas as pd
from bertopic import BERTopic
import re
import nltk
nltk.download('punkt_tab')
from nltk.tokenize import sent_tokenize
from sklearn.feature_extraction.text import CountVectorizer
from sentence_transformers import SentenceTransformer
from hdbscan import HDBSCAN
import openai
from bertopic.representation import KeyBERTInspired, MaximalMarginalRelevance, OpenAI, PartOfSpeech

[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\lukas\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


In [2]:
# Load data
df = pd.read_csv("../Data/ukraine_textcontain_after_new_preprocessed.csv")
df

Unnamed: 0                                      article_title  \
0             0  US can no longer be perfunctory toward Guterre...   
1             1  Healthy and stable China-S.Korea ties depend o...   
2             2  China’s power in the world, economically and p...   
3             3  Europe faces ‘coldest’ winter as energy crisis...   
4             4  Severe drought in Europe ‘further expanding an...   
..          ...                                                ...   
484         485  US policy of ‘technological apartheid’ could l...   
485         486  US behind global grain crises: Chinese FM spok...   
486         487  ‘No longer US’ backyard,’ Latin America sends ...   
487         488  Chinese envoy warns against providing weapons ...   
488         489  Ukraine, Moldova agree to facilitate border cr...   

                 author published_time  \
0          Global Times     2022-08-22   
1         Wang Junsheng     2022-08-23   
2          Global Times     2022-08-23   
3              Qi Xijia     2022-08-23   
4                   AFP     2022-08-23   
..                  ...            ...   
484       William Jones     2022-06-06   
485        Global Times     2022-06-07   
486  GT staff reporters     2022-06-07   
487              Xinhua     2022-06-07   
488              Xinhua     2022-06-07   

                                          article_text article_category_one  \
0    Since this year, the United Nations (UN) has r...              OPINION   
1    Wednesday marks the 30th anniversary of the es...              OPINION   
2    Editor's Note: For Chinese people, the past de...              OPINION   
3    A deepening energy crisis in Europe could put ...               SOURCE   
4    A severe drought hitting swathes of Europe is ...                WORLD   
..                                                 ...                  ...   
484  A New York Times article earlier this month do...              OPINION   
485  Zhao Lijian Photo: VCG  Each global grain cris...               SOURCE   
486  Mexico's President Andres Manuel Lopez Obrador...                WORLD   
487  A Chinese envoy on Monday warned against const...                CHINA   
488  The customs agencies of Ukraine and Moldova ha...                WORLD   

    article_category_two                                picture_description  \
0              EDITORIAL  United Nations Secretary-General Antonio Guter...   
1              VIEWPOINT                          Illustration: Chen Xia/GT   
2              VIEWPOINT             Tower Bridge, London, the UK Photo:VCG   
3                ECONOMY  A coal-fired power plant operated by German en...   
4                 EUROPE                      Picture description not found   
..                   ...                                                ...   
484            VIEWPOINT            Illustration: Tang Tengfei/Global Times   
485              ECONOMY                      Picture description not found   
486             AMERICAS                      Picture description not found   
487            DIPLOMACY                      Picture description not found   
488        CROSS-BORDERS                      Picture description not found   

                 author_title        author_description  
0    Author details not found  Author details not found  
1    Author details not found  Author details not found  
2    Author details not found  Author details not found  
3    Author details not found  Author details not found  
4    Author details not found  Author details not found  
..                        ...                       ...  
484  Author details not found  Author details not found  
485  Author details not found  Author details not found  
486  Author details not found  Author details not found  
487  Author details not found  Author details not found  
488  Author details not found  Author details not found  

[489 rows x 10 columns]

In [3]:
sentences = []
dates = []
for article, date in zip(df['article_text'], df['published_time']):
    sentence_cout = len(sentences)
    sentences.extend(sent_tokenize(str(article)))
    delta = len(sentences) - sentence_cout
    for _ in range(delta):
        dates.append(date)
sentences = [re.sub(r"[^a-zA-Z]+", " ", s) for s in sentences]

In [12]:
#prapare models
embedding_model = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = embedding_model.encode(sentences, show_progress_bar=True)
hdbscan_model = HDBSCAN(min_cluster_size=50, metric='euclidean', cluster_selection_method='eom', prediction_data=True)
vectorizer_model = CountVectorizer(stop_words="english")
# client = openai.OpenAI(api_key="sk-WuvQLP8aUps80YkLbDDRKYHCFi1k8SfHJ4VJF2-Ow0T3BlbkFJMkZXPa3NSyP9-nWqhxncLvIvJ5wOpctXxbOtvM0ioA")
# prompt = """
# I have a topic that contains the following documents:
# [DOCUMENTS]
# The topic is described by the following keywords: [KEYWORDS]
#
# Based on the information above, extract a short but highly descriptive topic label of at most 5 words. Make sure it is in the following format:
# topic: <topic label>
# """
# openai_model = OpenAI(client, model="gpt-3.5-turbo", delay_in_seconds=5, prompt=prompt)
representation_model = MaximalMarginalRelevance(diversity=0.2)

Batches:   0%|          | 0/398 [00:00<?, ?it/s]

In [13]:
# Create BERTopic model
topic_model = BERTopic(verbose=True, vectorizer_model=vectorizer_model, hdbscan_model=hdbscan_model, embedding_model=embedding_model, representation_model=representation_model)
topics, probs = topic_model.fit_transform(sentences)

2024-12-10 20:21:20,265 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/398 [00:00<?, ?it/s]

2024-12-10 20:23:04,991 - BERTopic - Embedding - Completed ✓
2024-12-10 20:23:04,992 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-12-10 20:23:22,534 - BERTopic - Dimensionality - Completed ✓
2024-12-10 20:23:22,535 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-12-10 20:23:23,078 - BERTopic - Cluster - Completed ✓
2024-12-10 20:23:23,084 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-12-10 20:23:24,515 - BERTopic - Representation - Completed ✓


In [14]:
topics_over_time = topic_model.topics_over_time(sentences,dates, nr_bins=20)

20it [00:22,  1.10s/it]


In [15]:
topics_over_time

Topic                                            Words  Frequency  \
0       -1  china, countries, products, belarusian, chinese        147   
1        0   countries, policy, violence, interests, global         42   
2        1          ukraine, russia, weapons, conflict, oil         62   
3        2             china, chinese, nations, zhang, guns         36   
4        3  farm, xinjiang, agricultural, bozhou, harvester          2   
..     ...                                              ...        ...   
492     18            covid, pandemic, hiatus, wave, visits          3   
493     20    nato, asia, destabilizing, establish, seeking          3   
494     22         committee, cpc, pandemic, jiechi, visits          1   
495     31    ali, champion, seconds, championships, garcia          4   
496     32        globaltimes, cn, com, opinion, globaltime          1   

                  Timestamp  
0   2022-06-05 22:07:40.800  
1   2022-06-05 22:07:40.800  
2   2022-06-05 22:07:40.800  
3   2022-06-05 22:07:40.800  
4   2022-06-05 22:07:40.800  
..                      ...  
492 2022-08-19 02:24:00.000  
493 2022-08-19 02:24:00.000  
494 2022-08-19 02:24:00.000  
495 2022-08-19 02:24:00.000  
496 2022-08-19 02:24:00.000  

[497 rows x 4 columns]

In [24]:
fig = topic_model.visualize_topics_over_time(topics_over_time, top_n_topics=10)
fig.write_image("topic_over_time.png")

In [17]:
#print topics
topic_model.get_topic_info()

Topic  Count                                      Name  \
0      -1   2910         -1_china_global_chinese_countries   
1       0   1713     0_world_countries_democracy_political   
2       1   1078             1_ukraine_russia_eu_sanctions   
3       2   1047       2_china_chinese_relations_countries   
4       3    873  3_xinjiang_institute_training_vocational   
5       4    660          4_taiwan_island_straits_mainland   
6       5    397               5_food_grain_ukraine_crisis   
7       6    356         6_brics_global_summit_cooperation   
8       7    313     7_japan_japanese_constitution_kishida   
9       8    287               8_pelosi_visit_taiwan_nancy   
10      9    280            9_inflation_fed_recession_yuan   
11     10    256           10_nato_expansion_soviet_warsaw   
12     11    228          11_climate_emissions_carbon_coal   
13     12    170          12_british_brexit_minister_sunak   
14     13    169           13_growth_percent_economy_china   
15     14    158                14_korea_korean_yoon_seoul   
16     15    148                15_india_border_china_nato   
17     16    139   16_africa_african_continent_cooperation   
18     17    131        17_eu_cooperation_baltic_relations   
19     18    131        18_covid_epidemic_quarantine_virus   
20     19    125            19_europe_european_autonomy_eu   
21     20    123            20_asia_pacific_nato_strategic   
22     21    123                21_biden_israel_iran_saudi   
23     22    122      22_asean_indonesia_ministers_meeting   
24     23    121                     23_kong_hong_law_city   
25     24    112          24_lanka_debt_economic_countries   
26     25     91        25_afghanistan_afghan_karzai_kabul   
27     26     80        26_xinjiang_genocide_region_ethnic   
28     27     70             27_sweden_nato_nordic_joining   
29     28     67        28_refugees_refugee_asylum_seekers   
30     29     64        29_freight_trains_customs_mongolia   
31     30     59         30_aircraft_carrier_carriers_navy   
32     31     59              31_meters_seconds_won_bronze   
33     32     58             32_globaltimes_cn_com_opinion   

                                       Representation  \
0   [china, global, chinese, countries, economic, ...   
1   [world, countries, democracy, political, secur...   
2   [ukraine, russia, eu, sanctions, oil, ukrainia...   
3   [china, chinese, relations, countries, russia,...   
4   [xinjiang, institute, training, vocational, ar...   
5   [taiwan, island, straits, mainland, chinese, i...   
6   [food, grain, ukraine, crisis, wheat, istanbul...   
7   [brics, global, summit, cooperation, emerging,...   
8   [japan, japanese, constitution, kishida, milit...   
9   [pelosi, visit, taiwan, nancy, chinese, counte...   
10  [inflation, fed, recession, yuan, rates, monet...   
11  [nato, expansion, soviet, warsaw, pact, strate...   
12  [climate, emissions, carbon, coal, renewable, ...   
13  [british, brexit, minister, sunak, conservativ...   
14  [growth, percent, economy, china, gdp, exports...   
15  [korea, korean, yoon, seoul, relations, suk, a...   
16  [india, border, china, nato, qian, interests, ...   
17  [africa, african, continent, cooperation, coun...   
18  [eu, cooperation, baltic, relations, latvia, c...   
19  [covid, epidemic, quarantine, virus, pandemic,...   
20  [europe, european, autonomy, eu, strategic, ge...   
21  [asia, pacific, nato, strategic, region, allia...   
22  [biden, israel, iran, saudi, arab, oil, gulf, ...   
23  [asean, indonesia, ministers, meeting, uzbekis...   
24  [kong, hong, law, city, government, democracy,...   
25  [lanka, debt, economic, countries, loans, lank...   
26  [afghanistan, afghan, karzai, kabul, taliban, ...   
27  [xinjiang, genocide, region, ethnic, xi, urumq...   
28  [sweden, nato, nordic, joining, swedish, turki...   
29  [refugees, refugee, asylum, seekers, rwanda, d...   
30  [freight, trains, customs, mongolia, railway, ...   
31  [airc

In [23]:
fig = topic_model.visualize_topics()
#save plotly png
fig.write_image("topic_distance.png")

In [19]:
topic_model.visualize_documents(sentences, embeddings=embeddings)